<a href="https://colab.research.google.com/github/Rashi2011/Rashi-Madhukar/blob/master/Programs%20in%20Tensorflow/spam_ham_TF.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [39]:
#Libraries
import tensorflow as tf
from tensorflow import keras
import numpy as np
import torch

In [2]:
#Spam-ham Dataset
#Loading the Dataset
from google.colab import files
uploaded = files.upload()

Saving spam_or_not_spam.csv to spam_or_not_spam.csv


In [3]:
import io 
import pandas as pd
dataset= pd.read_csv(io.BytesIO(uploaded['spam_or_not_spam.csv']), encoding= 'unicode_escape')

In [40]:
#Preprocessing Data
from sklearn.utils import shuffle
data = shuffle(dataset)
data.dropna(inplace=True)

#Dividing Data into input and output Format
print(data['email'].shape)
print(data['label'].shape)

sentence = data.iloc[:, 0]
label = data.iloc[:, 1].astype('int')
label = np.array(label)



(2999,)
(2999,)


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [41]:
#Tokenize
from tensorflow.keras.preprocessing.text import Tokenizer
#Tokenizing 1000 words and replacing unknown words with <oov> and Tokenizer also skips Punctuations
tokenizer = Tokenizer(num_words = 1000,oov_token = "<OOV>")
print(tokenizer)
tokenizer.fit_on_texts(data['email'])
print(tokenizer)
#Giving every token an index value 
word_index =  tokenizer.word_index
print(word_index)

{'<OOV>': 1, 'number': 2, 'the': 3, 'to': 4, 'and': 5, 'of': 6, 'a': 7, 'i': 8, 'url': 9, 'in': 10, 'is': 11, 'you': 12, 'that': 13, 'it': 14, 'for': 15, 'this': 16, 'on': 17, 's': 18, 'with': 19, 'be': 20, 'from': 21, 'have': 22, 'are': 23, 'not': 24, 't': 25, 'your': 26, 'as': 27, 'or': 28, 'if': 29, 'at': 30, 'but': 31, 'by': 32, 'can': 33, 'list': 34, 'we': 35, 'all': 36, 'an': 37, 'my': 38, 'was': 39, 'they': 40, 'will': 41, 'so': 42, 'do': 43, 'get': 44, 'more': 45, 'has': 46, 'there': 47, 'one': 48, 'out': 49, 'no': 50, 'just': 51, 'about': 52, 'what': 53, 'time': 54, 'our': 55, 'which': 56, 'only': 57, 'up': 58, 'like': 59, 'email': 60, 'use': 61, 'would': 62, 'people': 63, 'any': 64, 'free': 65, 'now': 66, 'their': 67, 'me': 68, 'some': 69, 'new': 70, 'who': 71, 'mail': 72, 'don': 73, 'here': 74, 'when': 75, 'm': 76, 'other': 77, 'been': 78, 'wrote': 79, 'e': 80, 'how': 81, 'he': 82, 'rpm': 83, 'than': 84, 'mailing': 85, 'date': 86, 'them': 87, 'message': 88, 'then': 89, 'also

In [42]:
#Text to Sequence
sequences = tokenizer.texts_to_sequences(data['email'])
print("word_index",word_index)
print("sequences",sequences)

word_index {'<OOV>': 1, 'number': 2, 'the': 3, 'to': 4, 'and': 5, 'of': 6, 'a': 7, 'i': 8, 'url': 9, 'in': 10, 'is': 11, 'you': 12, 'that': 13, 'it': 14, 'for': 15, 'this': 16, 'on': 17, 's': 18, 'with': 19, 'be': 20, 'from': 21, 'have': 22, 'are': 23, 'not': 24, 't': 25, 'your': 26, 'as': 27, 'or': 28, 'if': 29, 'at': 30, 'but': 31, 'by': 32, 'can': 33, 'list': 34, 'we': 35, 'all': 36, 'an': 37, 'my': 38, 'was': 39, 'they': 40, 'will': 41, 'so': 42, 'do': 43, 'get': 44, 'more': 45, 'has': 46, 'there': 47, 'one': 48, 'out': 49, 'no': 50, 'just': 51, 'about': 52, 'what': 53, 'time': 54, 'our': 55, 'which': 56, 'only': 57, 'up': 58, 'like': 59, 'email': 60, 'use': 61, 'would': 62, 'people': 63, 'any': 64, 'free': 65, 'now': 66, 'their': 67, 'me': 68, 'some': 69, 'new': 70, 'who': 71, 'mail': 72, 'don': 73, 'here': 74, 'when': 75, 'm': 76, 'other': 77, 'been': 78, 'wrote': 79, 'e': 80, 'how': 81, 'he': 82, 'rpm': 83, 'than': 84, 'mailing': 85, 'date': 86, 'them': 87, 'message': 88, 'then'

In [43]:
#Padding
from tensorflow.keras.preprocessing.sequence import pad_sequences
padded = pad_sequences(sequences,padding = 'post',maxlen = 30,truncating = 'post')
print(type(padded))

<class 'numpy.ndarray'>


In [53]:
#train_test_split
from sklearn.model_selection import train_test_split
train_sentence,test_sentence,train_label,test_label = train_test_split(padded,label,test_size = 0.2,random_state = 0)
train_sentence_ = tf.convert_to_tensor(train_sentence)
test_sentence = tf.convert_to_tensor(test_sentence)
train_label = tf.convert_to_tensor(train_label)
test_label = tf.convert_to_tensor(test_label)
print(train_sentence.shape,train_label.shape,test_sentence.shape,test_label.shape)


(2399, 30) (2399,) (600, 30) (600,)


In [88]:
#defining the Model
model = tf.keras.Sequential([
                             tf.keras.layers.Embedding(1000,64,input_length =30),
                             tf.keras.layers.Flatten(),
                             tf.keras.layers.Dense(6,activation = 'relu'),
                             tf.keras.layers.Dense(1,activation = 'sigmoid')
])

In [89]:
#Compile 
model.compile(optimizer = 'rmsprop', loss = 'binary_crossentropy',metrics = ['acc'])

In [90]:
#Fit the Model
num_epochs = 10
model.fit(train_sentence,train_label,epochs =  num_epochs,validation_data = (test_sentence,test_label))


Epoch 1/10
75/75 [==============================] - 0s 4ms/step - loss: 0.3706 - acc: 0.8441 - val_loss: 0.2876 - val_acc: 0.8583
Epoch 2/10
75/75 [==============================] - 0s 3ms/step - loss: 0.1968 - acc: 0.9200 - val_loss: 0.1800 - val_acc: 0.9400
Epoch 3/10
75/75 [==============================] - 0s 3ms/step - loss: 0.1224 - acc: 0.9742 - val_loss: 0.1325 - val_acc: 0.9517
Epoch 4/10
75/75 [==============================] - 0s 3ms/step - loss: 0.0685 - acc: 0.9867 - val_loss: 0.0928 - val_acc: 0.9633
Epoch 5/10
75/75 [==============================] - 0s 3ms/step - loss: 0.0322 - acc: 0.9958 - val_loss: 0.0710 - val_acc: 0.9683
Epoch 6/10
75/75 [==============================] - 0s 3ms/step - loss: 0.0167 - acc: 0.9971 - val_loss: 0.0799 - val_acc: 0.9667
Epoch 7/10
75/75 [==============================] - 0s 2ms/step - loss: 0.0082 - acc: 0.9996 - val_loss: 0.0726 - val_acc: 0.9700
Epoch 8/10
75/75 [==============================] - 0s 3ms/step - loss: 0.0037 - acc: 1.00

In [93]:
input_text = [['hi,this is Rashi and i am her to just see whether it is working or not important text to u an your family, concerning money wealth and bank details'],['looking for property in spain don_t waste your time that is what most people do when they look for property using property web sites why because many of the properties that are advertised on them have already been sold you could waste precious time looking for and inquiring after properties that have already been sold how frustrating the property market is moving very fast here in spain and frankly many estate agents do not have the time to update their web sites what you need is a company that can find you property that is actually for sale and can present to you a selection of current properties that specifically fit your requirements just think of how much time and effort that would save you property finders spain can do just that we are here in spain and have a many ways of looking for property that has just arrived on the market even looking in the local papers so while others are chasing properties or new projects that are no longer for sale you can be viewing property that has just arrived on the market simply fill in the form below and press the send button and we will do all of the hard work for you once we receive your requirements we will immediately begin looking for current properties just right for you property finders form property type villa apartment town house new building projects plot of land number of bedrooms NUMBER NUMBER NUMBER NUMBER NUMBER NUMBER location do you want a sea view yes no don t care mountain view yes no don t care a property in the country a property in or near a city pool yes no yes no don t care price range are you planning to come to spain in the next three months yes no yes no name e mail address telephone number country code let us find a property for you ']]
#Tokenize
tokenizer1 = Tokenizer(num_words = 100,oov_token = "<OOV>")
tokenizer1.fit_on_texts(input_text)
print(tokenizer1)

index = tokenizer1.word_index
print(index) 

#Text to sequence
sequence = tokenizer1.texts_to_sequences(input_text)
print(sequences)

#Padded 
padded1 = pad_sequences(sequence,padding = 'post',maxlen = 30,truncating = 'post')
padded1 = tf.convert_to_tensor(padded1)
print(padded1.shape)


{'<OOV>': 1, 'hi,this is rashi and i am her to just see whether it is working or not important text to u an your family, concerning money wealth and bank details': 2, 'looking for property in spain don_t waste your time that is what most people do when they look for property using property web sites why because many of the properties that are advertised on them have already been sold you could waste precious time looking for and inquiring after properties that have already been sold how frustrating the property market is moving very fast here in spain and frankly many estate agents do not have the time to update their web sites what you need is a company that can find you property that is actually for sale and can present to you a selection of current properties that specifically fit your requirements just think of how much time and effort that would save you property finders spain can do just that we are here in spain and have a many ways of looking for property that has just arrived 

In [94]:
#Prediction
model.predict(padded1)

array([[0.7313132],
       [0.2002784]], dtype=float32)